In [59]:
from pymongo import MongoClient
import pandas as pd
import requests
import src.func as fc


## Dataset set-up

Initial query to filter by the most important parameter: companies created in the 2000s; that have not closed and with coordinates of their offices.

In [28]:
client = MongoClient("mongodb://localhost/companies")
db = client.get_database()

In [29]:
query = {"$and": [{
    "founded_year": {"$gte":2000}}, {
    "founded_year": {"$lte": 2010}}, {
    "deadpooled_year": None}, {
    "offices": {
        "$not": {
            "$size": 0
        }
    }
}]}

mydb = list(db["companies"].find(query,{"name":1,
                                        "founded_year":1,
                                        "offices":1, 
                                        "category_code": 1,
                                        "number_of_employees":1, 
                                        "_id":0}))

In [30]:
df = pd.DataFrame(mydb)

df.head()

name category_code  number_of_employees  founded_year  \
0         Digg          news                 60.0          2004   
1         Geni           web                 18.0          2006   
2  StumbleUpon           web                  NaN          2002   
3       Gizmoz           web                  NaN          2003   
4     Facebook        social               5299.0          2004   

                                             offices  
0  [{'description': None, 'address1': '135 Missis...  
1  [{'description': 'Headquarters', 'address1': '...  
2  [{'description': '', 'address1': '', 'address2...  
3  [{'description': None, 'address1': None, 'addr...  
4  [{'description': 'Headquarters', 'address1': '...

Processing to obtain the "location" column of the "point" type to generate GeoIndex in MongoDB.

In [31]:
df = df.explode("offices")
dfOfficeData = df[["offices"]].apply(lambda r: r.offices, result_type="expand", axis=1)


In [32]:
cleanData = pd.concat([df,dfOfficeData], axis=1)
cleanData.head()

name category_code  number_of_employees  founded_year  \
0         Digg          news                 60.0          2004   
1         Geni           web                 18.0          2006   
2  StumbleUpon           web                  NaN          2002   
2  StumbleUpon           web                  NaN          2002   
3       Gizmoz           web                  NaN          2003   

                                             offices   description  \
0  {'description': None, 'address1': '135 Mississ...          None   
1  {'description': 'Headquarters', 'address1': '9...  Headquarters   
2  {'description': '', 'address1': '', 'address2'...                 
2  {'description': '', 'address1': '', 'address2'...                 
3  {'description': None, 'address1': None, 'addre...          None   

               address1 address2 zip_code            city state_code  \
0    135 Mississippi St             94107   San Francisco         CA   
1  9229 W. Sunset Blvd.             90069  West Hollywood         CA   
2                                           San Francisco         CA   
2                                           New York City         NY   
3                  None     None     None      Menlo Park         CA   

  country_code   latitude   longitude  
0          USA  37.764726 -122.394523  
1          USA  34.090368 -118.393064  
2          USA  37.775196 -122.419204  
2          USA        NaN         NaN  
3          USA  37.484130 -122.169472

The records with NaN values in their coordinates and the columns that are not interesting me are removed.

In [33]:
cleanData = cleanData.copy().dropna(subset=["latitude", "longitude"]) 
cleanData = cleanData.drop(columns=["offices", "address1", "address2"]) #¿Por que hay que eliminarla en este paso y no después?

In [36]:
def asGeoJSON(lat,lng):
    try:
        lat = float(lat)
        lng = float(lng)
        if not math.isnan(lat) and not math.isnan(lng):
            return {
                "type":"Point",
                "coordinates":[lng,lat]
            }
    except Exception:
        print("Invalid data")
        return None
        
cleanData["location"] = cleanData[["latitude","longitude"]].apply(lambda x:asGeoJSON(x.latitude,x.longitude), axis=1)
cleanData[["latitude","longitude","location"]]

latitude   longitude                                           location
0     37.764726 -122.394523  {'type': 'Point', 'coordinates': [-122.394523,...
1     34.090368 -118.393064  {'type': 'Point', 'coordinates': [-118.393064,...
2     37.775196 -122.419204  {'type': 'Point', 'coordinates': [-122.419204,...
3     37.484130 -122.169472  {'type': 'Point', 'coordinates': [-122.169472,...
4     37.416050 -122.151801  {'type': 'Point', 'coordinates': [-122.151801,...
...         ...         ...                                                ...
8352  29.848779  -95.504545  {'type': 'Point', 'coordinates': [-95.5045451,...
8353  37.701940 -121.936698  {'type': 'Point', 'coordinates': [-121.9366984...
8354  47.088219    8.437163  {'type': 'Point', 'coordinates': [8.4371634, 4...
8356  40.793024  -74.323554  {'type': 'Point', 'coordinates': [-74.3235539,...
8357  33.407786  -86.761302  {'type': 'Point', 'coordinates': [-86.7613019,...

[6834 rows x 3 columns]

In [37]:
cleanData.head()

name category_code  number_of_employees  founded_year   description  \
0         Digg          news                 60.0          2004          None   
1         Geni           web                 18.0          2006  Headquarters   
2  StumbleUpon           web                  NaN          2002                 
3       Gizmoz           web                  NaN          2003          None   
4     Facebook        social               5299.0          2004  Headquarters   

  zip_code            city state_code country_code   latitude   longitude  \
0    94107   San Francisco         CA          USA  37.764726 -122.394523   
1    90069  West Hollywood         CA          USA  34.090368 -118.393064   
2            San Francisco         CA          USA  37.775196 -122.419204   
3     None      Menlo Park         CA          USA  37.484130 -122.169472   
4    94025      Menlo Park         CA          USA  37.416050 -122.151801   

                                            location  
0  {'type': 'Point', 'coordinates': [-122.394523,...  
1  {'type': 'Point', 'coordinates': [-118.393064,...  
2  {'type': 'Point', 'coordinates': [-122.419204,...  
3  {'type': 'Point', 'coordinates': [-122.169472,...  
4  {'type': 'Point', 'coordinates': [-122.151801,...

In [38]:
dfCoordenates = cleanData.copy()
cleanData = cleanData.drop(columns=["latitude", "longitude"])
cleanData.to_json("output/cleaned_offices.json", orient="records")

## Where in Europe?

In [39]:
import geopandas as gpd
from geopandas import GeoDataFrame
from shapely.geometry import Point

from cartoframes.viz import Map, Layer
from cartoframes.viz.helpers import size_continuous_layer
from cartoframes.viz.widgets import histogram_widget

In [51]:
def geoDataFrame(df):
    geometry = [Point(xy) for xy in zip(df.longitude, df.latitude)]
    crs = {"init": "epsg:4326"}
    gdf = GeoDataFrame(df, crs=crs, geometry=geometry)
    return gdf

geodf = geoDataFrame(dfCoordenates)

type(geodf)

geopandas.geodataframe.GeoDataFrame

In [52]:
Map(Layer(geodf), viewport={'zoom': 3.26, 'lat': 50.556628, 'lng': 10.135056})

In [56]:
londondf = geodf[geodf["city"] == "London"]
berlindf = geodf[geodf["city"] == "Berlin"]
amsterdamdf = geodf[geodf["city"] == "Amsterdam"]

len(londondf), len(berlindf), len(amsterdamdf)

(213, 62, 41)

I want to do the analysis in Europe because of their higher standard of living. Although not anymore, London represents the European city and has a good pool of companies compared to the second in the ranking, Berlin.

In [57]:
display(londondf.head())

name    category_code  number_of_employees  founded_year  \
61     KickApps       enterprise                 72.0          2004   
117      spigit         software                120.0          2006   
198  Curverider  network_hosting                  5.0          2005   
222        Zopa          finance                  NaN          2005   
237    Covestor          finance                  NaN          2005   

    description zip_code    city state_code country_code   latitude  \
61    UK Office  W1J 9HF  London       None          GBR  51.509473   
117              W1W 8RL  London       None          GBR  51.517038   
198              W1J 7BU  London       None          GBR  51.785428   
222              W1T 1QD  London       None          GBR  51.517904   
237      London  W1W 6AN  London       None          GBR  51.519420   

     longitude                                           location  \
61   -0.135624  {'type': 'Point', 'coordinates': [-0.1356235, ...   
117  -0.139476  {'type': 'Point', 'coordinates': [-0.1394759, ...   
198  -1.197534  {'type': 'Point', 'coordinates': [-1.197534, 5...   
222  -0.139947  {'type': 'Point', 'coordinates': [-0.139947, 5...   
237  -0.143369  {'type': 'Point', 'coordinates': [-0.1433689, ...   

                      geometry  
61   POINT (-0.13562 51.50947)  
117  POINT (-0.13948 51.51704)  
198  POINT (-1.19753 51.78543)  
222  POINT (-0.13995 51.51790)  
237  POINT (-0.14337 51.51942)

## Google API

In [66]:
import os
import json
from dotenv import load_dotenv
load_dotenv()

Python-dotenv could not parse statement starting at line 2


True

How many Starbucks are near every company?

In [72]:
def starbucks250m(val):
    API_key = os.getenv('API_KEY')
    lat = val["coordinates"][1]
    lon = val["coordinates"][0]
    base_url = "https://maps.googleapis.com/maps/api/place/textsearch/json?"
    endpoint = "query=starbucks&location={0},{1}&radius=250&key={2}".format(lat, lon, API_key)
    res = requests.get(base_url+endpoint).json()
    number = len(res["results"])
    return number

In [74]:
londondf['Starbucks'] = londondf.apply(lambda x: starbucks250m(x["location"]), axis=1)

/home/linuxbrew/.linuxbrew/opt/python/lib/python3.7/site-packages/ipykernel_launcher.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  """Entry point for launching an IPython kernel.


Design agencies in London

In [76]:
def design():
    API_key = os.getenv('API_KEY')
    base_url = "https://maps.googleapis.com/maps/api/place/textsearch/json?"
    endpoint = "query=design+agency+in+london&key={}".format(API_key)
    res = requests.get(base_url+endpoint).json()
    return res

In [82]:
# The whole JSON document
design = design()
with open('output/design.json', 'w', encoding='utf-8') as f:
    json.dump(design, f, ensure_ascii=False, indent=4)

In [83]:
# The "results" array --> My collection

design2 = design["results"]
with open('output/design2.json', 'w', encoding='utf-8') as f:
    json.dump(design2, f, ensure_ascii=False, indent=4)

In [84]:
client = MongoClient("mongodb://localhost/design2")
db = client.get_database()

In [85]:
mydb = list(db["design2"].find(projection = {"name":1,
                                        "geometry":1,
                                        }))

In [86]:
df = pd.DataFrame(mydb)

df.head()

_id  \
0  5e4251eabc5847a39c59a485   
1  5e4251eabc5847a39c59a486   
2  5e4251eabc5847a39c59a487   
3  5e4251eabc5847a39c59a488   
4  5e4251eabc5847a39c59a489   

                                            geometry  \
0  {'location': {'lat': 51.5238508, 'lng': -0.076...   
1  {'location': {'lat': 51.52266119999999, 'lng':...   
2  {'location': {'lat': 51.5041254, 'lng': -0.079...   
3  {'location': {'lat': 51.4790202, 'lng': -0.199...   
4  {'location': {'lat': 51.5372076, 'lng': -6.879...   

                                                name  
0      Evolve Branding and Creative Agency in London  
1                             Brand Design in London  
2  Top Branding and Design Agency in London- Spur...  
3                              Consultants in Design  
4                               London Design Agency

In [88]:
dfGeometry = df[["geometry"]].apply(lambda r: r.geometry, result_type="expand", axis=1)

In [89]:
dfGeometry

location  \
0    {'lat': 51.5238508, 'lng': -0.07681099999999999}   
1       {'lat': 51.52266119999999, 'lng': -0.1031967}   
2    {'lat': 51.5041254, 'lng': -0.07981189999999999}   
3              {'lat': 51.4790202, 'lng': -0.1995988}   
4   {'lat': 51.5372076, 'lng': -6.879999999999999e...   
5              {'lat': 51.5266198, 'lng': -0.0800414}   
6              {'lat': 51.5464922, 'lng': -0.0511709}   
7              {'lat': 51.5273195, 'lng': -0.0888947}   
8              {'lat': 51.5147519, 'lng': -0.0722078}   
9              {'lat': 51.5267875, 'lng': -0.0965553}   
10       {'lat': 51.52382000000001, 'lng': -0.076907}   
11             {'lat': 51.6079356, 'lng': -0.2078007}   
12             {'lat': 51.5175581, 'lng': -0.1804577}   
13             {'lat': 51.5199744, 'lng': -0.1558212}   
14      {'lat': 51.52475370000001, 'lng': -0.0833085}   
15   {'lat': 51.5231438, 'lng': -0.09882089999999999}   
16             {'lat': 51.5038449, 'lng': -0.1003608}   
17             {'lat': 51.5178986, 'lng': -0.1327214}   
18        {'lat': 51.51121300000001, 'lng': -0.12675}   
19             {'lat': 51.5202523, 'lng': -0.0731351}   

                                             viewport  
0   {'northeast': {'lat': 51.52510042989272, 'lng'...  
1   {'northeast': {'lat': 51.52396932989272, 'lng'...  
2   {'northeast': {'lat': 51.50541327989273, 'lng'...  
3   {'northeast': {'lat': 51.48040902989272, 'lng'...  
4   {'northeast': {'lat': 51.53851732989272, 'lng'...  
5   {'northeast': {'lat': 51.52796302989272, 'lng'...  
6   {'northeast': {'lat': 51.54785057989272, 'lng'...  
7   {'northeast': {'lat': 51.52873597989272, 'lng'...  
8   {'northeast': {'lat': 51.51618442989272, 'lng'...  
9   {'northeast': {'lat': 51.52812787989271, 'lng'...  
10  {'northeast': {'lat': 51.52517352989272, 'lng'...  
11  {'northeast': {'lat': 51.60928767989272, 'lng'...  
12  {'northeast': {'lat': 51.51875992989272, 'lng'...  
13  {'northeast': {'lat': 51.52132437989272, 'lng'...  
14  {'northeast': {'lat': 51.52606737989272, 'lng'...  
15  {'northeast': {'lat': 51.52457237989272, 'lng'...  
16  {'northeast': {'lat': 51.50523932989272, 'lng'...  
17  {'northeast': {'lat': 51.51920952989271, 'lng'...  
18  {'northeast': {'lat': 51.51254632989273, 'lng'...  
19  {'northeast': {'lat': 51.52162702989273, 'lng'...

In [90]:
cleanData = pd.concat([df,dfGeometry], axis=1)
cleanData.head()

_id  \
0  5e4251eabc5847a39c59a485   
1  5e4251eabc5847a39c59a486   
2  5e4251eabc5847a39c59a487   
3  5e4251eabc5847a39c59a488   
4  5e4251eabc5847a39c59a489   

                                            geometry  \
0  {'location': {'lat': 51.5238508, 'lng': -0.076...   
1  {'location': {'lat': 51.52266119999999, 'lng':...   
2  {'location': {'lat': 51.5041254, 'lng': -0.079...   
3  {'location': {'lat': 51.4790202, 'lng': -0.199...   
4  {'location': {'lat': 51.5372076, 'lng': -6.879...   

                                                name  \
0      Evolve Branding and Creative Agency in London   
1                             Brand Design in London   
2  Top Branding and Design Agency in London- Spur...   
3                              Consultants in Design   
4                               London Design Agency   

                                            location  \
0   {'lat': 51.5238508, 'lng': -0.07681099999999999}   
1      {'lat': 51.52266119999999, 'lng': -0.1031967}   
2   {'lat': 51.5041254, 'lng': -0.07981189999999999}   
3             {'lat': 51.4790202, 'lng': -0.1995988}   
4  {'lat': 51.5372076, 'lng': -6.879999999999999e...   

                                            viewport  
0  {'northeast': {'lat': 51.52510042989272, 'lng'...  
1  {'northeast': {'lat': 51.52396932989272, 'lng'...  
2  {'northeast': {'lat': 51.50541327989273, 'lng'...  
3  {'northeast': {'lat': 51.48040902989272, 'lng'...  
4  {'northeast': {'lat': 51.53851732989272, 'lng'...

In [91]:
cleanData = cleanData.drop(columns=["geometry", "_id",  "viewport"])

name  \
0       Evolve Branding and Creative Agency in London   
1                              Brand Design in London   
2   Top Branding and Design Agency in London- Spur...   
3                               Consultants in Design   
4                                London Design Agency   
5                     Klinical - Design Agency London   
6                             Spinach Branding Agency   
7           ikon | Boutique Branding Agency in London   
8                             London Creative Designs   
9                                       Fabrik Brands   
10  Rebellion London - Advertising, Branding & Des...   
11                         Fishfinger Creative Agency   
12                             AB The Creative Agency   
13              Grain Creative Branding and Marketing   
14                                  SomeOne in London   
15                     Kota - Creative Digital Agency   
16                                               Deep   
17                                             Recipe   
18                                  Chaos Design Ltd.   
19                                    Huddle Creative   

                                             location  
0    {'lat': 51.5238508, 'lng': -0.07681099999999999}  
1       {'lat': 51.52266119999999, 'lng': -0.1031967}  
2    {'lat': 51.5041254, 'lng': -0.07981189999999999}  
3              {'lat': 51.4790202, 'lng': -0.1995988}  
4   {'lat': 51.5372076, 'lng': -6.879999999999999e...  
5              {'lat': 51.5266198, 'lng': -0.0800414}  
6              {'lat': 51.5464922, 'lng': -0.0511709}  
7              {'lat': 51.5273195, 'lng': -0.0888947}  
8              {'lat': 51.5147519, 'lng': -0.0722078}  
9              {'lat': 51.5267875, 'lng': -0.0965553}  
10       {'lat': 51.52382000000001, 'lng': -0.076907}  
11             {'lat': 51.6079356, 'lng': -0.2078007}  
12             {'lat': 51.5175581, 'lng': -0.1804577}  
13             {'lat': 51.5199744, 'lng': -0.1558212}  
14      {'lat': 51.52475370000001, 'lng': -0.0833085}  
15   {'lat': 51.5231438, 'lng': -0.09882089999999999}  
16             {'lat': 51.5038449, 'lng': -0.1003608}  
17             {'lat': 51.5178986, 'lng': -0.1327214}  
18        {'lat': 51.51121300000001, 'lng': -0.12675}  
19             {'lat': 51.5202523, 'lng': -0.0731351}